In [1]:
# Based on examples at: https://github.com/interpretml/interpret?tab=readme-ov-file

In [2]:
# Install, as necessary
# !pip install interpret

# Interpret Library's Example - Adult Dataset

In [3]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

In [4]:
# Interpret specific
from interpret import set_visualize_provider
from interpret.provider import InlineProvider
set_visualize_provider(InlineProvider())

In [5]:
# Get data
df = pd.read_csv(
    "https://archive.ics.uci.edu/ml/machine-learning-databases/adult/adult.data",
    header=None)

In [6]:
df.columns = [
    "Age", "WorkClass", "fnlwgt", "Education", "EducationNum",
    "MaritalStatus", "Occupation", "Relationship", "Race", "Gender",
    "CapitalGain", "CapitalLoss", "HoursPerWeek", "NativeCountry", "Income"
]
X = df.iloc[:, :-1]
y = (df.iloc[:, -1] == " >50K").astype(int)

In [7]:
# Prepare data
seed = 42
np.random.seed(seed)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=seed)

In [8]:
X

Age          WorkClass  fnlwgt    Education  EducationNum  \
0       39          State-gov   77516    Bachelors            13   
1       50   Self-emp-not-inc   83311    Bachelors            13   
2       38            Private  215646      HS-grad             9   
3       53            Private  234721         11th             7   
4       28            Private  338409    Bachelors            13   
...    ...                ...     ...          ...           ...   
32556   27            Private  257302   Assoc-acdm            12   
32557   40            Private  154374      HS-grad             9   
32558   58            Private  151910      HS-grad             9   
32559   22            Private  201490      HS-grad             9   
32560   52       Self-emp-inc  287927      HS-grad             9   

             MaritalStatus          Occupation    Relationship    Race  \
0            Never-married        Adm-clerical   Not-in-family   White   
1       Married-civ-spouse     Exec-managerial         Husband   White   
2                 Divorced   Handlers-cleaners   Not-in-family   White   
3       Married-civ-spouse   Handlers-cleaners         Husband   Black   
4       Married-civ-spouse      Prof-specialty            Wife   Black   
...                    ...                 ...             ...     ...   
32556   Married-civ-spouse        Tech-support            Wife   White   
32557   Married-civ-spouse   Machine-op-inspct         Husband   White   
32558              Widowed        Adm-clerical       Unmarried   White   
32559        Never-married        Adm-clerical       Own-child   White   
32560   Married-civ-spouse     Exec-managerial            Wife   White   

        Gender  CapitalGain  CapitalLoss  HoursPerWeek   NativeCountry  
0         Male         2174            0            40   United-States  
1         Male            0            0            13   United-States  
2         Male            0            0            40   United-States  
3         Male            0            0            40   United-States  
4       Female            0            0            40            Cuba  
...        ...          ...          ...           ...             ...  
32556   Female            0            0            38   United-States  
32557     Male            0            0            40   United-States  
32558   Female            0            0            40   United-States  
32559     Male            0            0            20   United-States  
32560   Female        15024            0            40   United-States  

[32561 rows x 14 columns]

In [9]:
y

0        0
1        0
2        0
3        0
4        0
        ..
32556    0
32557    1
32558    0
32559    0
32560    1
Name: Income, Length: 32561, dtype: int64

In [10]:
# Now train a model
from interpret.glassbox import ExplainableBoostingClassifier
ebm = ExplainableBoostingClassifier()
ebm.fit(X_train, y_train)

ExplainableBoostingClassifier()

In [11]:
# We can ask to explain
from interpret import show
show(ebm.explain_global())

In [13]:
# Local explanation
show(ebm.explain_local(X_test[:5], y_test[:5]), 0)

# Blackbox explanations via LIME in Intepret package

In [14]:
# loading libraries
from sklearn.ensemble import RandomForestClassifier
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline

In [15]:
# We have to transform categorical variables to use sklearn models
X = pd.get_dummies(X, prefix_sep='.').astype(float)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=seed)

In [16]:
# Blackbox system can include preprocessing, not just a classifier! Example
#  showed including PCA but we don't
rf = RandomForestClassifier(random_state=seed)

blackbox_model = Pipeline([ ('rf', rf) ])
blackbox_model.fit(X_train, y_train)


Pipeline(steps=[('rf', RandomForestClassifier(random_state=42))])

In [18]:
from interpret.blackbox import LimeTabular
from interpret import show

lime = LimeTabular(blackbox_model, X_train, random_state=seed)
show(lime.explain_local(X_test[:5], y_test[:5]), 0)

# Explanations via multiple methods

In [19]:
# Based on: https://interpret.ml/docs/lr.html  (logistic regression)
# - and https://interpret.ml/docs/dt.html (decision tree)

In [20]:
from interpret import set_visualize_provider
from interpret.provider import InlineProvider
set_visualize_provider(InlineProvider())

In [21]:
# Running on cancer data
import numpy as np
from sklearn.datasets import load_breast_cancer
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score


In [22]:
# Using DT
from interpret.glassbox import ClassificationTree
from interpret import show


In [23]:
seed = 42
np.random.seed(seed)
X, y = load_breast_cancer(return_X_y=True, as_frame=True)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=seed)

dt = ClassificationTree(random_state=seed)
dt.fit(X_train, y_train)

auc = roc_auc_score(y_test, dt.predict_proba(X_test)[:, 1])
print("AUC: {:.3f}".format(auc))


AUC: 0.957


In [24]:
show(dt.explain_global())

In [25]:
# Using LR
from interpret.glassbox import LogisticRegression
from interpret import show

In [26]:
seed = 42
np.random.seed(seed)
X, y = load_breast_cancer(return_X_y=True, as_frame=True)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=seed)

lr = LogisticRegression(max_iter=3000, random_state=seed)
lr.fit(X_train, y_train)

auc = roc_auc_score(y_test, lr.predict_proba(X_test)[:, 1])
print("AUC: {:.3f}".format(auc))


AUC: 0.998


In [27]:
show(lr.explain_global())